In [10]:
# Importing the required libraries
import credentials as cd


from fyers_apiv3 import fyersModel


import pandas as pd


import datetime as dt

In [11]:
# Reading the access token from the file
with open("access.txt", "r") as a:

    access_token = a.read()


client_id = cd.client_id


# Initialize the FyersModel instance with your client_id, access_token, and enable async mode


fyers = fyersModel.FyersModel(
    client_id=client_id, is_async=False, token=access_token, log_path=""
)

In [12]:
# Fetching the historical data for Nifty 50 index for 5 minutes interval for the month of May 2024 using the history API endpoint of Fyers API
data = {
    "symbol": "NSE:NIFTY50-INDEX",
    "resolution": "5",
    "date_format": "1",
    "range_from": "2024-05-01",
    "range_to": "2024-05-30",
    "cont_flag": "1",
}


response = fyers.history(data=data)
# print(response)
data = response["candles"]
df = pd.DataFrame(data)
print(df)

              0         1         2         3         4  5
0    1714621500  22567.85  22659.95  22567.85  22649.05  0
1    1714621800  22650.05  22662.20  22626.35  22649.55  0
2    1714622100  22648.35  22654.75  22618.80  22639.95  0
3    1714622400  22640.00  22668.40  22624.85  22633.50  0
4    1714622700  22632.85  22648.35  22618.45  22632.50  0
..          ...       ...       ...       ...       ... ..
960  1716274800  22530.85  22544.90  22530.85  22542.70  0
961  1716275100  22543.10  22551.80  22542.95  22549.05  0
962  1716275400  22548.95  22556.80  22544.30  22553.55  0
963  1716275700  22553.45  22562.10  22550.75  22557.90  0
964  1716276000  22558.00  22565.95  22557.20  22565.45  0

[965 rows x 6 columns]


In [13]:
# Converting the UNIX timestamp to datetime format and setting the date column as the index of the dataframe and saving the data to a CSV file
df.columns = ["date", "open", "high", "low", "close", "volume"]


df["date"] = pd.to_datetime(df["date"], unit="s")


df.date = df.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
print(df)


df["date"] = df["date"].dt.tz_localize(None)


df = df.set_index("date")

# # Resample the data to business day frequency, using forward fill to handle the missing values
# df = df.resample("B").ffill()

print(df)
df.to_csv("data.csv")


print(dt.datetime.now())

                         date      open      high       low     close  volume
0   2024-05-02 09:15:00+05:30  22567.85  22659.95  22567.85  22649.05       0
1   2024-05-02 09:20:00+05:30  22650.05  22662.20  22626.35  22649.55       0
2   2024-05-02 09:25:00+05:30  22648.35  22654.75  22618.80  22639.95       0
3   2024-05-02 09:30:00+05:30  22640.00  22668.40  22624.85  22633.50       0
4   2024-05-02 09:35:00+05:30  22632.85  22648.35  22618.45  22632.50       0
..                        ...       ...       ...       ...       ...     ...
960 2024-05-21 12:30:00+05:30  22530.85  22544.90  22530.85  22542.70       0
961 2024-05-21 12:35:00+05:30  22543.10  22551.80  22542.95  22549.05       0
962 2024-05-21 12:40:00+05:30  22548.95  22556.80  22544.30  22553.55       0
963 2024-05-21 12:45:00+05:30  22553.45  22562.10  22550.75  22557.90       0
964 2024-05-21 12:50:00+05:30  22558.00  22565.95  22557.20  22565.45       0

[965 rows x 6 columns]
                         open      high 

In [14]:
import mplfinance as mpf

# Set the plot style
mc = mpf.make_marketcolors(up="tab:blue", down="tab:red")
s = mpf.make_mpf_style(marketcolors=mc)

# Create the plot
mpf.plot(
    df,
    type="candle",
    style=s,
    title="Nifty 50 Index",
    ylabel="Price",
    figratio=(20, 10),
    savefig=dict(fname="nifty50.png", dpi=100),
)

c:\Users\Shiva Kumar G\AppData\Local\Programs\Python\Python312\Lib\site-packages\mplfinance\_arg_validators.py:84: UserWarning: 


            POSSIBLE TO SEE DETAILS (Candles, Ohlc-Bars, Etc.)
   For more information see:
   - https://github.com/matplotlib/mplfinance/wiki/Plotting-Too-Much-Data
   
   TO SILENCE THIS WARNING, set `type='line'` in `mpf.plot()`
   OR set kwarg `warn_too_much_data=N` where N is an integer 
   LARGER than the number of data points you want to plot.

  warnings.warn('\n\n ================================================================= '+


In [15]:
import numpy as np

# Calculate MACD and Signal line
df["macd"] = (
    df["close"].ewm(span=9, adjust=False).mean()
    - df["close"].ewm(span=13, adjust=False).mean()
)
df["signal"] = df["macd"].ewm(span=9, adjust=False).mean()

# Calculate RSI
delta = df["close"].diff()
up, down = delta.copy(), delta.copy()
up[up < 0] = 0
down[down > 0] = 0
average_gain = up.rolling(window=14).mean()
average_loss = abs(down.rolling(window=14).mean())
rs = average_gain / average_loss
df["rsi"] = 100 - (100 / (1 + rs))

# Calculate fast and slow EMA
df["fast_ema"] = df["close"].ewm(span=9, adjust=False).mean()
df["slow_ema"] = df["close"].ewm(span=13, adjust=False).mean()

# Calculate MACD Histogram
df["macd_histogram"] = df["macd"] - df["signal"]

# Define trade signals
df["macd_signal"] = np.where(df["macd"] > df["signal"], 1, -1)
df["ema_signal"] = np.where(df["fast_ema"] > df["slow_ema"], 1, -1)

# Calculate previous high and low
df["prev_high"] = df["high"].shift()
df["prev_low"] = df["low"].shift()

# Define breakout signals
df["bullish_breakout"] = np.where(df["high"] > df["prev_high"], 1, 0)
df["bearish_breakout"] = np.where(df["low"] < df["prev_low"], 1, 0)

# Identify sideways market periods
df["sideways_market"] = np.where(
    (df["macd_histogram"] > -2) & (df["macd_histogram"] < 2), 1, 0
)

# Define a threshold for the distance from the fast_ema
threshold = 1.01  # Adjust this value based on your needs

# Calculate the distance from the fast_ema
df["distance_from_fast_ema"] = df["close"] - df["fast_ema"]

# Define entry signals
df["entry_signal"] = np.where(
    (df["macd_signal"].shift() == 1)
    & (df["ema_signal"].shift() == 1)
    & (df["bullish_breakout"].shift() == 1)
    & (df["sideways_market"].shift() == 0),
    1,
    np.where(
        (df["macd_signal"].shift() == -1)
        & (df["ema_signal"].shift() == -1)
        & (df["bearish_breakout"].shift() == 1)
        & (df["sideways_market"].shift() == 0),
        -1,
        0,
    ),
)


import pyti.average_directional_index as adx

# Calculate ADX
df["adx"] = adx.average_directional_index(df["high"], df["low"], df["close"], period=14)


# Function to generate trade signals
def generate_trade_signal(
    entry_signal, previous_trade_signal, distance_from_fast_ema, adx, previous_adx
):
    if entry_signal != 0:  # if there's an entry signal, follow it
        return entry_signal
    elif (
        (previous_trade_signal == 1)
        and (distance_from_fast_ema < -threshold)
        and (adx >= previous_adx)
    ):
        return -1
    elif (
        (previous_trade_signal == -1)
        and (distance_from_fast_ema > threshold)
        and (adx >= previous_adx)
    ):
        return 1
    else:
        return previous_trade_signal  # keep the previous signal if the trend continues


df["previous_adx"] = df["adx"].shift()

# Initialize the 'trade_signal' column
df["trade_signal"] = 0

df["previous_trade_signal"] = df["trade_signal"].shift()

df["trade_signal"] = df.apply(
    lambda row: generate_trade_signal(
        row["entry_signal"],
        row["previous_trade_signal"],
        row["distance_from_fast_ema"],
        row["adx"],
        row["previous_adx"],
    ),
    axis=1,
)

# Export the 'trade_signal' column to a CSV file
df["trade_signal"].to_csv("trade_signals.csv", header=True)

df.tail()

ModuleNotFoundError: No module named 'pyti.average_directional_index'

In [91]:
import mplfinance as mpf

# Create a new series for the buy signals that is the same length as df["close"]
buy_signals = np.where(
    (df["trade_signal"][-500:] == 1) & (df["bullish_breakout"][-500:] == 1),
    df["close"][-500:],
    np.nan,
)

# Create a new series for the sell signals that is the same length as df["close"]
sell_signals = np.where(
    (df["trade_signal"][-500:] == -1) & (df["bearish_breakout"][-500:] == 1),
    df["close"][-500:],
    np.nan,
)


# Create the subplots
apds = [
    mpf.make_addplot(df["macd"][-500:], panel=1, color="b", secondary_y="auto"),
    mpf.make_addplot(df["signal"][-500:], panel=1, color="r", secondary_y="auto"),
    mpf.make_addplot(
        df["macd_histogram"][-500:], panel=1, color="g", secondary_y="auto", type="bar"
    ),
    mpf.make_addplot(df["rsi"][-500:], panel=2, color="g", secondary_y="auto"),
    mpf.make_addplot(
        df["fast_ema"][-500:], color="g"
    ),  # Plot on the same panel as the price
    mpf.make_addplot(
        df["slow_ema"][-500:], color="r"
    ),  # Plot on the same panel as the price
    mpf.make_addplot(
        buy_signals, scatter=True, markersize=200, marker="^", color="g"
    ),  # Buy signals
    mpf.make_addplot(
        sell_signals, scatter=True, markersize=200, marker="v", color="r"
    ),  # Sell signals
]

# Create the plot
mpf.plot(
    df[-500:],
    type="candle",
    style="yahoo",
    addplot=apds,
    title="Nifty 50 Index",
    ylabel="Price",
    figratio=(20, 10),
    yscale="log",
    savefig=dict(fname="nifty50_strategy.png", dpi=100),
)

In [89]:
# Check if there are any buy signals
print("Buy signals:", (df["trade_signal"] == 1).sum())

# Check if there are any sell signals
print("Sell signals:", (df["trade_signal"] == -1).sum())

Buy signals: 88
Sell signals: 60


In [90]:
# Define transaction cost
transaction_cost = 0.001  # 0.1%

# Create a new column that contains the price at which you buy or sell
df["trade_price"] = np.where(
    df["trade_signal"] == 1, df["close"] * (1 + transaction_cost), np.nan
)
df["trade_price"] = np.where(
    df["trade_signal"] == -1, df["close"] * (1 - transaction_cost), df["trade_price"]
)

# Forward fill this column to simulate holding the bought stock
df["trade_price"].ffill(inplace=True)

# Calculate the percentage change in this column to get the return of your strategy
df["return"] = df["trade_price"].pct_change()

# The total return of the strategy is the product of these returns
total_return = (1 + df["return"]).prod() - 1

print("Total return:", total_return)

Total return: -0.0033431596004084296


C:\Users\Shiva Kumar G\AppData\Local\Temp\ipykernel_16564\294477634.py:13: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df["trade_price"].ffill(inplace=True)


In [ ]:
# draw plot

import matplotlib.pyplot as plt

plt.plot(df["close"], label="Close Price", color="black")
plt.plot(df["fast_ema"], label="Fast EMA", color="red")
plt.plot(df["slow_ema"], label="Slow EMA", color="blue")
plt.show()

In [ ]:
# define entries

df["Long"] = df.fast_ema > df.slow_ema
df.tail()

Step-by-Step Trading Strategy
1. Setup Indicators
    a. MACD (Moving Average Convergence Divergence):
        * MACD Line: 9-period EMA minus 13-period EMA.
        * Signal Line: 9-period EMA of the MACD Line.
        * Histogram: MACD Line minus Signal Line.
    b. Exponential Moving Averages (EMAs):
        9-period EMA.
        13-period EMA.
Relative Strength Index (RSI):
14-period RSI.
2. Identify the Trend Using MACD
Bullish Trend:
When the MACD Line crosses above the Signal Line.
Bearish Trend:
When the MACD Line crosses below the Signal Line.
3. Secondary Confirmation with EMA Crossover
Bullish Confirmation:
The 9 EMA crosses above the 13 EMA.
Bearish Confirmation:
The 9 EMA crosses below the 13 EMA.
4. Use RSI for Entry and Exit Signals
Entry Signal (Bullish):
RSI is above 30 and trending upwards (indicating increasing momentum).
Exit Signal (Bullish):
RSI is above 70 (indicating overbought conditions, potential reversal).
Entry Signal (Bearish):
RSI is below 70 and trending downwards (indicating decreasing momentum).
Exit Signal (Bearish):
RSI is below 30 (indicating oversold conditions, potential reversal).
Trading Strategy Rules
Long Position (Buying)
MACD Signal:
Wait for the MACD Line to cross above the Signal Line.
EMA Confirmation:
Wait for the 9 EMA to cross above the 13 EMA.
RSI Check:
Ensure RSI is above 30 and trending upwards.
Entry:
Enter a long position when all the above conditions are met.
Exit:
Exit the position when RSI reaches above 70 or when the 9 EMA crosses below the 13 EMA.
Short Position (Selling)
MACD Signal:
Wait for the MACD Line to cross below the Signal Line.
EMA Confirmation:
Wait for the 9 EMA to cross below the 13 EMA.
RSI Check:
Ensure RSI is below 70 and trending downwards.
Entry:
Enter a short position when all the above conditions are met.
Exit:
Exit the position when RSI drops below 30 or when the 9 EMA crosses above the 13 EMA.
Example Workflow
Entering a Long Trade:
MACD Crossover:
MACD Line crosses above the Signal Line on the daily chart.
EMA Confirmation:
A few days later, the 9 EMA crosses above the 13 EMA.
RSI Check:
RSI is at 40 and moving upwards.
Enter Trade:
Enter a long position.
Monitoring:
Monitor the RSI and EMAs regularly.
Exit Trade:
Exit the position when RSI reaches 70 or when 9 EMA crosses below 13 EMA.
Entering a Short Trade:
MACD Crossover:
MACD Line crosses below the Signal Line on the daily chart.
EMA Confirmation:
A few days later, the 9 EMA crosses below the 13 EMA.
RSI Check:
RSI is at 60 and moving downwards.
Enter Trade:
Enter a short position.
Monitoring:
Monitor the RSI and EMAs regularly.
Exit Trade:
Exit the position when RSI drops to 30 or when 9 EMA crosses above 13 EMA.

In [ ]:
# pip install pandas numpy ta matplotlib

In [90]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ta


def compute_indicators(data):
    # Compute the 9 and 13 period EMAs
    data["9_EMA"] = ta.trend.ema_indicator(data["close"], window=9)
    data["13_EMA"] = ta.trend.ema_indicator(data["close"], window=13)

    # Compute the MACD using 9 and 13 period EMAs
    data["MACD_Line"] = ta.trend.ema_indicator(
        data["close"], window=9
    ) - ta.trend.ema_indicator(data["close"], window=13)
    data["Signal_Line"] = ta.trend.ema_indicator(data["MACD_Line"], window=9)
    data["MACD_Hist"] = data["MACD_Line"] - data["Signal_Line"]

    # Compute the RSI
    data["RSI"] = ta.momentum.rsi(data["close"], window=14)

    return data


def generate_signals(data):
    data["Signal"] = 0
    data["Position"] = 0

    for i in range(1, len(data)):
        # Long position entry conditions
        if (
            data["MACD_Line"].iloc[i] > data["Signal_Line"].iloc[i]
            and data["9_EMA"].iloc[i] > data["13_EMA"].iloc[i]
            and data["RSI"].iloc[i] > 30
        ):
            data["Signal"].iloc[i] = 1
        # Long position exit conditions
        elif (
            data["RSI"].iloc[i] >= 70 or data["9_EMA"].iloc[i] < data["13_EMA"].iloc[i]
        ):
            data["Signal"].iloc[i] = -1
        # Short position entry conditions
        elif (
            data["MACD_Line"].iloc[i] < data["Signal_Line"].iloc[i]
            and data["9_EMA"].iloc[i] < data["13_EMA"].iloc[i]
            and data["RSI"].iloc[i] < 70
        ):
            data["Signal"].iloc[i] = -1
        # Short position exit conditions
        elif (
            data["RSI"].iloc[i] <= 30 or data["9_EMA"].iloc[i] > data["13_EMA"].iloc[i]
        ):
            data["Signal"].iloc[i] = 1

    data["Position"] = data["Signal"].replace(to_replace=0, method="ffill")

    return data


def plot_data(data):
    plt.figure(figsize=(14, 10))

    # Plot close price and EMAs
    plt.subplot(3, 1, 1)
    plt.plot(data["close"], label="close Price", color="blue")
    plt.plot(data["9_EMA"], label="9 EMA", color="orange")
    plt.plot(data["13_EMA"], label="13 EMA", color="green")
    plt.legend()
    plt.title("close Price and EMAs")

    # Plot MACD
    plt.subplot(3, 1, 2)
    plt.plot(data["MACD_Line"], label="MACD Line", color="blue")
    plt.plot(data["Signal_Line"], label="Signal Line", color="orange")
    plt.bar(data.index, data["MACD_Hist"], label="MACD Histogram", color="green")
    plt.legend()
    plt.title("MACD")

    # Plot RSI
    plt.subplot(3, 1, 3)
    plt.plot(data["RSI"], label="RSI", color="blue")
    plt.axhline(70, color="red", linestyle="--")
    plt.axhline(30, color="green", linestyle="--")
    plt.legend()
    plt.title("RSI")

    plt.tight_layout()
    plt.show()


def main():
    # Load data (example uses Yahoo Finance CSV format)
    # data = pd.read_csv("path_to_your_data.csv", parse_dates=True, index_col="Date")
    data = df

    # Compute indicators
    data = compute_indicators(data)

    # Generate signals
    data = generate_signals(data)

    # Plot data and signals
    plot_data(data)


if __name__ == "__main__":
    main()

C:\Users\Shiva Kumar G\AppData\Local\Temp\ipykernel_15056\1788305780.py:53: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  data["Signal"].iloc[i] = 1
C:\Users\Shiva Kumar G\AppData\Local\Temp\ipykernel_15056\1788305780.py:53: SettingWithCopyW

<IPython.core.display.Javascript object>

In [89]:
import pandas as pd
import backtrader as bt
import matplotlib.pyplot as plt


class MACDEMA_RSI_Strategy(bt.Strategy):
    params = (
        ("macd1", 9),
        ("macd2", 13),
        ("macdsig", 9),
        ("ema1", 9),
        ("ema2", 13),
        ("rsi_period", 14),
    )

    def __init__(self):
        self.macd = bt.ind.MACD(
            self.data.close,
            period_me1=self.params.macd1,
            period_me2=self.params.macd2,
            period_signal=self.params.macdsig,
        )
        self.macd_line = self.macd.macd
        self.signal_line = self.macd.signal

        self.ema1 = bt.ind.EMA(self.data.close, period=self.params.ema1)
        self.ema2 = bt.ind.EMA(self.data.close, period=self.params.ema2)

        self.rsi = bt.ind.RSI(self.data.close, period=self.params.rsi_period)

        self.order = None

        self.signals = []
        self.macd_crossed_above = False
        self.macd_crossed_below = False

    def next(self):
        if self.order:
            return

        signal = None

        if self.macd_line > self.signal_line and not self.macd_crossed_above:
            self.macd_crossed_above = True
            self.macd_crossed_below = False
        elif self.macd_line < self.signal_line and not self.macd_crossed_below:
            self.macd_crossed_below = True
            self.macd_crossed_above = False

        if self.position:
            if (self.rsi > 70) or (self.ema1 < self.ema2):
                self.order = self.sell()
                signal = "Sell"
                self.macd_crossed_above = False
                self.macd_crossed_below = False
                print(f"Sell signal at {self.data.datetime.date(0)}")
        else:
            if self.macd_crossed_above and self.ema1 > self.ema2:
                self.order = self.buy()
                signal = "Buy"
                self.macd_crossed_above = False
                print(f"Buy signal at {self.data.datetime.date(0)}")
            elif self.macd_crossed_below and self.ema1 < self.ema2:
                self.order = self.sell()
                signal = "Sell"
                self.macd_crossed_below = False
                print(f"Sell signal at {self.data.datetime.date(0)}")

        if signal:
            self.signals.append(
                {
                    "date": self.data.datetime.date(0).isoformat(),
                    "signal": signal,
                    "close": self.data.close[0],
                    "macd_line": self.macd_line[0],
                    "signal_line": self.signal_line[0],
                    "ema1": self.ema1[0],
                    "ema2": self.ema2[0],
                    "rsi": self.rsi[0],
                }
            )

    def stop(self):
        df = pd.DataFrame(self.signals)
        df.to_csv("signals.csv", index=False)
        print("Signals exported to signals.csv")


class TradeList(bt.Analyzer):
    def __init__(self):
        self.trades = []

    def notify_trade(self, trade):
        if trade.isclosed:
            self.trades.append(
                {
                    "date": self.strategy.data.datetime.date().isoformat(),
                    "direction": "Buy" if trade.history[0].event.size > 0 else "Sell",
                    "price": trade.history[0].event.price,
                    "size": trade.size,
                    "profit": trade.pnl,
                    "profit_percent": trade.pnlcomm
                    / self.strategy.broker.getvalue()
                    * 100,
                }
            )

    def get_analysis(self):
        return self.trades


def print_trade_analysis(analyzer):
    trades = analyzer.get_analysis()
    if not trades:
        print("No trades were made.")
        return

    df = pd.DataFrame(trades)
    df.to_csv("trade_log.csv", index=False)
    print("Trade log exported to trade_log.csv")
    print(df)


def plot_signals(data, signals):
    plt.figure(figsize=(14, 7))

    plt.plot(data.index, data["close"], label="Close Price")

    buy_signals = signals[signals["signal"] == "Buy"]
    plt.plot(
        buy_signals["date"],
        buy_signals["close"],
        "^",
        markersize=10,
        color="g",
        label="Buy Signal",
    )

    sell_signals = signals[signals["signal"] == "Sell"]
    plt.plot(
        sell_signals["date"],
        sell_signals["close"],
        "v",
        markersize=10,
        color="r",
        label="Sell Signal",
    )

    plt.legend()
    plt.show()


def main():
    global df
    data = df
    data_bt = bt.feeds.PandasData(dataname=data)
    cerebro = bt.Cerebro()

    cerebro.addstrategy(MACDEMA_RSI_Strategy)
    cerebro.adddata(data_bt)
    cerebro.broker.set_cash(100000)
    cerebro.broker.setcommission(commission=0.001)
    cerebro.addanalyzer(bt.analyzers.SharpeRatio, _name="sharpe")
    cerebro.addanalyzer(bt.analyzers.DrawDown, _name="drawdown")
    cerebro.addanalyzer(bt.analyzers.Returns, _name="returns")
    cerebro.addanalyzer(TradeList, _name="tradelist")

    print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())
    results = cerebro.run()
    strat = results[0]

    print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())
    print("Sharpe Ratio:", strat.analyzers.sharpe.get_analysis()["sharperatio"])
    print("Max Drawdown:", strat.analyzers.drawdown.get_analysis().max.drawdown)
    print("Total Returns:", strat.analyzers.returns.get_analysis()["rnorm100"])

    print_trade_analysis(strat.analyzers.tradelist)
    cerebro.plot()

    signals = pd.read_csv("signals.csv", parse_dates=["date"])
    plot_signals(data, signals)


if __name__ == "__main__":
    main()

Starting Portfolio Value: 100000.00
Sell signal at 2024-03-02
Signals exported to signals.csv
Final Portfolio Value: 99874.30
Sharpe Ratio: None
Max Drawdown: 1.0636744673716283
Total Returns: -0.6195864882288665
No trades were made.


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
df.tail()

In [ ]:
# # due to API restriction, data can't fetched for more than 60 days at a time, so we need to fetch data in chunks of 60 days and then concatenate them to get the complete data
# def fetchOHLC(ticker, interval, duration):
#     """extracts historical data and outputs in the form of dataframe"""
#     instrument = ticker
#     data = {
#         "symbol": instrument,
#         "resolution": interval,
#         "date_format": "1",
#         "range_from": dt.date.today() - dt.timedelta(duration),
#         "range_to": dt.date.today(),
#         "cont_flag": "1",
#     }
#     sdata = fyers.history(data)
#     sdata = pd.DataFrame(sdata["candles"])
#     sdata.columns = ["date", "open", "high", "low", "close", "volume"]
#     sdata["date"] = pd.to_datetime(sdata["date"], unit="s")
#     sdata.date = sdata.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
#     sdata["date"] = sdata["date"].dt.tz_localize(None)
#     sdata = sdata.set_index("date")
#     return sdata


# ticker = "NSE:NIFTYBANK-INDEX"
# data = fetchOHLC(ticker, "D", 60)
# print(data)


# def gethistory(symbol1, type, duration):
#     symbol = "NSE:" + symbol1 + "-" + type
#     start = dt.date.today() - dt.timedelta(duration)
#     end = dt.date.today() - dt.timedelta()
#     sdata = pd.DataFrame()
#     while start <= end:
#         end2 = start + dt.timedelta(60)
#         data = {
#             "symbol": symbol,
#             "resolution": "1",
#             "date_format": "1",
#             "range_from": start,
#             "range_to": end2,
#             "cont_flag": "1",
#         }
#         s = fyers.history(data)
#         s = pd.DataFrame(s["candles"])
#         sdata = pd.concat([sdata, s], ignore_index=True)
#         start = end2 + dt.timedelta(1)
#     sdata.columns = ["date", "open", "high", "low", "close", "volume"]
#     sdata["date"] = pd.to_datetime(sdata["date"], unit="s")
#     sdata.date = sdata.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
#     sdata["date"] = sdata["date"].dt.tz_localize(None)
#     sdata = sdata.set_index("date")
#     return sdata


# data = gethistory("NIFTYBANK", "INDEX", 3000)
# print(data)
# data.to_csv("niftybank.csv")